In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, BatchNormalization
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from tensorflow.keras.regularizers import l2
from sklearn.preprocessing import StandardScaler, PowerTransformer
from tensorflow.keras.optimizers import Adam
import numpy as np
import joblib
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the CSV files
combined_df = pd.read_csv("/Github/DeepLforConcreteReuse/data/combined_csv_file.csv")
#print(combined_df.head())
combined_df.describe()

in:Inventory  in:Wall Length  in:Wall Height       in:Door  \
count  10080.000000    10080.000000    10080.000000  10080.000000   
mean       1.500000      600.000000      270.000000      0.375000   
std        1.118089      163.307417       24.496113      0.279522   
min        0.000000      400.000000      240.000000      0.000000   
25%        0.750000      400.000000      240.000000      0.187500   
50%        1.500000      600.000000      270.000000      0.375000   
75%        2.250000      800.000000      300.000000      0.562500   
max        3.000000      800.000000      300.000000      0.750000   

       in:Curve Frequency  in:Curve Amplitude  out:Leftover inventory[m2]  \
count        10080.000000        10080.000000                10080.000000   
mean             5.500000            3.600000                  831.002716   
std              2.156493            1.959689                  387.640828   
min              1.000000            0.000000                   46.193750   
25%              4.000000            2.000000                  476.329481   
50%              6.000000            4.000000                  829.299459   
75%              8.000000            6.000000                 1192.146452   
max              8.000000            6.000000                 1435.143476   

       out:Displacement Average[cm]  out:Uncovered Wall Area[m2]  \
count                  10080.000000                 10080.000000   
mean                     121.111512                   116.295327   
std                       69.304962                    92.186947   
min                        1.132252                     2.673025   
25%                       69.232180                    60.884997   
50%                      122.442751                    91.770552   
75%                      172.234519                   148.388786   
max                      350.894746                   534.509386   

       out:Average Mapping Tolerance  
count                   10080.000000  
mean                        0.132211  
std                         0.156921  
min                         0.000000  
25%                         0.021448  
50%                         0.060605  
75%                         0.203717  
max                         1.305005

In [14]:
cols = 3  # Number of columns in each row of subplots
rows = (len(combined_df.columns) + cols - 1) // cols  # Calculate rows needed

# Create subplots
fig = make_subplots(rows=rows, cols=cols, subplot_titles=combined_df.columns)

# Add a histogram to each subplot cell
for i, column in enumerate(combined_df.columns, 1):
    trace = go.Histogram(x=combined_df[column], nbinsx=30) 
    row = (i - 1) // cols + 1
    col = (i - 1) % cols + 1
    fig.add_trace(trace, row=row, col=col)

# Update layout (optional)
fig.update_layout(height=800, width=1000, title_text="Histograms of Data")
fig.show()

In [62]:
# Import necessary libraries
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Specify targets and features
targets = [
    'out:Leftover inventory[m2]', 
    'out:Displacement Average[cm]', 
    'out:Uncovered Wall Area[m2]', 
    'out:Average Mapping Tolerance'
]
features = [
    'in:Inventory', 
    'in:Wall Length', 
    'in:Wall Height', 
    'in:Door', 
    'in:Curve Frequency', 
    'in:Curve Amplitude'
]

# Define colors for each target
colors = {
    'out:Leftover inventory[m2]': 'rgba(178, 24, 43, 1)',        # Deep red
    'out:Displacement Average[cm]': 'rgba(214, 96, 77, 1)',     # Soft red
    'out:Uncovered Wall Area[m2]': 'rgba(33, 102, 172, 1)',      # Deep blue
    'out:Average Mapping Tolerance': 'rgba(67, 147, 195, 1)'     # Soft blue
}

# Assuming combined_df is your DataFrame containing the data
ta = combined_df[targets]

# Set the layout for 1 row and 4 columns
cols = 4
rows = 1

# Create subplots with titles
fig = make_subplots(
    rows=rows, 
    cols=cols, 
    subplot_titles=ta.columns,
    horizontal_spacing=0.1  # Adjust spacing between subplots
)

# Add a histogram to each subplot cell with specified colors and borders
for i, column in enumerate(ta.columns, 1):
    trace = go.Histogram(
        x=ta[column],
        nbinsx=30,
        marker=dict(
            color=colors[column],
            line=dict(
                color='black',  # Add black border around bars
                width=1         # Border thickness
            )
        ),
        name=column,
        opacity=0.7
    )
    row = 1  # Fixed to the single row
    col = i  # Each subplot goes in the next column
    fig.add_trace(trace, row=row, col=col)

# Update layout for better appearance
fig.update_layout(
    height=400,  # Adjust height for a single row
    width=1600,  # Adjust width for four subplots
    template='plotly_white',
    title=dict(
        text="Histograms of Target Data",
        x=0.5,  # Center align the title
        font=dict(size=20)  # Title font size
    ),
    font=dict(size=14),  # Font size for axes and titles
    #margin=dict(l=40, r=40, t=60, b=40),  # Adjust margins
    showlegend=False  # Hide legend if not needed
)

# Update axes labels and add consistent style
for i in range(1, len(ta.columns) + 1):
    fig.update_xaxes(
        title_text="Value",
        row=1, col=i,
        showline=True, linewidth=1.5, linecolor='black',  # Add axis line
        ticks="outside", tickwidth=1.5, tickcolor='black'
    )
    fig.update_yaxes(
        title_text="Count",
        row=1, col=i,
        showline=True, linewidth=1.5, linecolor='black',
        ticks="outside", tickwidth=1.5, tickcolor='black'
    )

# Display the figure
fig.show()

In [53]:
# Histograms of Yeo-Johnson Transformed & Standard Scaled Data
# Specify targets and features
targets = ['out:Leftover inventory[m2]', 'out:Displacement Average[cm]', 'out:Uncovered Wall Area[m2]', 'out:Average Mapping Tolerance']
features = ['in:Inventory', 'in:Wall Length', 'in:Wall Height', 'in:Door', 'in:Curve Frequency', 'in:Curve Amplitude'] 

# Splitting data into training and testing sets
X_train, X_test, Y_train, Y_test = train_test_split(combined_df[features], combined_df[targets], test_size=0.2, random_state=42)

# Apply Yeo-Johnson Transformation to targets
scaler_yeo = PowerTransformer(method='yeo-johnson', standardize=False)
Y_train_trans = scaler_yeo.fit_transform(Y_train)

# Apply StandardScaler
scaler_features = StandardScaler()
scaler_targets = StandardScaler()
X_train_scaled = scaler_features.fit_transform(X_train)
Y_train_scaled = scaler_targets.fit_transform(Y_train_trans)

# Convert the transformed data back to a DataFrame
Y_train_sc = pd.DataFrame(Y_train_scaled, columns=Y_train.columns, index=Y_train.index)

# Number of columns and rows in the grid
cols = 2
rows = (len(Y_train_sc.columns) + cols - 1) // cols  # Calculate rows needed

# Colors for each attribute
colors = {
    'out:Leftover inventory[m2]': 'rgba(178, 24, 43, 1)',  # Deep red
    'out:Displacement Average[cm]': 'rgba(214, 96, 77, 1)',  # Soft red
    'out:Uncovered Wall Area[m2]': 'rgba(33, 102, 172, 1)',  # Deep blue
    'out:Average Mapping Tolerance': 'rgba(67, 147, 195, 1)'  # Soft blue
}

# Create subplots
fig = make_subplots(
    rows=rows, cols=cols, 
    subplot_titles=Y_train_sc.columns,
    horizontal_spacing=0.1, vertical_spacing=0.2  # Adjust spacing between subplots
)

# Add a histogram to each subplot cell with black borders around bars
for i, column in enumerate(Y_train_sc.columns, 1):
    trace = go.Histogram(
        x=Y_train_sc[column],
        name=column,
        marker=dict(
            color=colors[column],
            line=dict(
                color='black',  # Add black borders
                width=1         # Border thickness
            )
        ),
        nbinsx=30,
        opacity=0.7
    )
    row = (i - 1) // cols + 1
    col = (i - 1) % cols + 1
    fig.add_trace(trace, row=row, col=col)

# Update layout
fig.update_layout(
    height=800,
    width=1000,
    title_text="Histograms of Yeo-Johnson Transformed & Standard Scaled Data",
    template='plotly_white',
    font=dict(size=14),  # Adjust font size for better readability
    showlegend=False,
    margin=dict(l=40, r=40, t=60, b=40),  # Adjust margins for a clean layout
)

# Update axes labels and add neat spacing
for i in range(1, len(Y_train_sc.columns) + 1):
    row = (i - 1) // cols + 1
    col = (i - 1) % cols + 1
    fig.update_xaxes(
        title_text="Transformed Value",
        row=row, col=col,
        showline=True, linewidth=1.5, linecolor='black',
        ticks="outside", tickwidth=1.5, tickcolor='black'
    )
    fig.update_yaxes(
        title_text="Count",
        row=row, col=col,
        showline=True, linewidth=1.5, linecolor='black',
        ticks="outside", tickwidth=1.5, tickcolor='black'
    )

# Show the plot
fig.show()

In [20]:
# Specify targets and features
targets = ['out:Leftover inventory[m2]', 'out:Displacement Average[cm]', 'out:Uncovered Wall Area[m2]', 'out:Average Mapping Tolerance']
features = ['in:Inventory', 'in:Wall Length', 'in:Wall Height', 'in:Door', 'in:Curve Frequency', 'in:Curve Amplitude'] 

# Splitting data into training and testing sets
X_train, X_test, Y_train, Y_test = train_test_split(combined_df[features], combined_df[targets], test_size=0.2, random_state=42)

# Apply log transformation to targets
# Adding 1 to avoid log(0) which is undefined
# Y_train_log = Y_train.apply(lambda x: np.log(x + 1) if np.issubdtype(x.dtype, np.number) else x)

# Initialize the PowerTransformer
scaler_yeo = PowerTransformer(method='yeo-johnson', standardize=False) 

# Fit and transform the target data
Y_train_trans = scaler_yeo.fit_transform(Y_train)

# Initialize StandardScaler
scaler_features = StandardScaler()
scaler_targets = StandardScaler()

# Fit and transform features
X_train_scaled = scaler_features.fit_transform(X_train)
Y_train_scaled = scaler_targets.fit_transform(Y_train_trans)

# Fit and transform targets
#Y_test_log = Y_test.apply(lambda x: np.log(x + 1) if np.issubdtype(x.dtype, np.number) else x)
#Y_test_trans = scaler_yeo.transform(Y_test)
#Y_test_scaled = scaler_targets.transform(Y_test_trans)

# Save the scaler for later use
#joblib.dump(scaler, 'X:/My Drive/CEA/PhD/Code/ACADIA24/scaler.save')
joblib.dump(scaler_yeo, '/Users/boenalan/Library/CloudStorage/GoogleDrive-boenalan@ethz.ch/My Drive/CEA/PhD/ACADIA24/TAD/scaler_yeo.pkl')
joblib.dump(scaler_features, '/Users/boenalan/Library/CloudStorage/GoogleDrive-boenalan@ethz.ch/My Drive/CEA/PhD/ACADIA24/TAD/scaler_features.pkl')
joblib.dump(scaler_targets, '/Users/boenalan/Library/CloudStorage/GoogleDrive-boenalan@ethz.ch/My Drive/CEA/PhD/ACADIA24/TAD/scaler_targets.pkl')

['/Users/boenalan/Library/CloudStorage/GoogleDrive-boenalan@ethz.ch/My Drive/CEA/PhD/ACADIA24/TAD/scaler_targets.pkl']

In [21]:
# Initialize callbacks
early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=5, min_lr=0.0001)

# Define model architecture with Batch Normalization and L2 Regularization
model = Sequential([
    Dense(128, input_dim=X_train.shape[1], activation='relu', kernel_regularizer=l2(0.01)),
    BatchNormalization(),
    Dropout(0.2),
    Dense(64, activation='relu', kernel_regularizer=l2(0.01)),
    BatchNormalization(),
    Dropout(0.2),
    Dense(Y_train.shape[1], activation='linear')  # Assuming a regression problem
])

# Compile model
model.compile(loss='mean_squared_error', optimizer=Adam(learning_rate=0.001)) #log spaced 0.01 up to 0.00001

# Fit model with callbacks
history = model.fit(X_train_scaled, Y_train_scaled, validation_split=0.1, epochs=100, batch_size=32, verbose=1,
                    callbacks=[early_stopping, reduce_lr])

# Save your model
model.save('/Users/boenalan/Library/CloudStorage/GoogleDrive-boenalan@ethz.ch/My Drive/CEA/PhD/ACADIA24/TAD/model.keras')

print('Model saved.')

Epoch 1/100


/opt/anaconda3/envs/tad/lib/python3.9/site-packages/keras/src/layers/core/dense.py:87: UserWarning:

Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.



227/227 ━━━━━━━━━━━━━━━━━━━━ 1s 964us/step - loss: 2.3322 - val_loss: 1.2761 - learning_rate: 0.0010
Epoch 2/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 595us/step - loss: 1.2003 - val_loss: 0.7665 - learning_rate: 0.0010
Epoch 3/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 666us/step - loss: 0.8333 - val_loss: 0.5373 - learning_rate: 0.0010
Epoch 4/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 797us/step - loss: 0.5903 - val_loss: 0.3995 - learning_rate: 0.0010
Epoch 5/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 751us/step - loss: 0.4422 - val_loss: 0.3078 - learning_rate: 0.0010
Epoch 6/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 713us/step - loss: 0.3373 - val_loss: 0.2542 - learning_rate: 0.0010
Epoch 7/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 660us/step - loss: 0.2735 - val_loss: 0.2120 - learning_rate: 0.0010
Epoch 8/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 608us/step - loss: 0.2320 - val_loss: 0.1576 - learning_rate: 0.0010
Epoch 9/100
227/227 ━━━━━━━━━━━━━━━━━━━━ 0s 594us/step - loss: 0.2150 - val_loss: 0.1426 - learning_rate: 0.

In [25]:
import plotly.graph_objects as go
import pandas as pd

# Assuming history.history contains 'loss' and 'val_loss'
epochs = range(1, len(history.history['loss']) + 1)
loss_df = pd.DataFrame({
    'Epoch': epochs,
    'Training Loss': history.history['loss'],
    'Validation Loss': history.history['val_loss']
})

# Define colors from the RdBu colorscale
# Red (higher values on the 'coolwarm' scale) for validation loss
# Blue (lower values on the 'coolwarm' scale) for training loss
#color_training = 'rgba(67, 147, 195, 1)'  # Soft blue
#color_validation = 'rgba(214, 96, 77, 1)'  # Soft red

# Create the figure
fig = go.Figure()

# Add traces for each dataset
fig.add_trace(go.Scatter(x=loss_df['Epoch'], y=loss_df['Training Loss'], mode='lines',
                         name='Training Loss'))
fig.add_trace(go.Scatter(x=loss_df['Epoch'], y=loss_df['Validation Loss'], mode='lines',
                         name='Validation Loss'))

# Add traces for each dataset
# fig.add_trace(go.Scatter(x=loss_df['Epoch'], y=loss_df['Training Loss'], mode='lines',
#                          name='Training Loss', line=dict(color=color_training)))
# fig.add_trace(go.Scatter(x=loss_df['Epoch'], y=loss_df['Validation Loss'], mode='lines',
#                          name='Validation Loss', line=dict(color=color_validation)))

# Update the layout to add titles and axis labels
fig.update_layout(
    title='Model Loss Over Epochs',
    height=600, width=1000,
    xaxis_title='Epoch',
    yaxis_title='Loss',
    template='plotly_white',  # This sets the background to white
    legend=dict(
            x=1,
            y=1,
            xanchor='right',
            yanchor='bottom',
            orientation='h',
            # bgcolor='rgba(255, 255, 255, 0.5)'  # Optional: adding a background color for clarity
        ),
    font=dict(color='black', size=18),  # Ensure text is black and adjust size as needed
        # Adding a plot border
        xaxis=dict(showline=True, linewidth=2, linecolor='black'),
        yaxis=dict(showline=True, linewidth=2, linecolor='black')
    )

# Show the plot
fig.show()

In [ ]:
from sklearn.metrics import mean_squared_error, r2_score

# Evaluate Neural Network
# Predict and inverse transform to original scale
X_test_scaled = scaler_features.transform(X_test) 
scaled_pred = model.predict(X_test_scaled)
#nn_predictions = np.exp(scaler_targets.inverse_transform(scaled_pred)) - 1

# Convert predictions from array back to DataFrame with proper column names
scaled_pred_df = pd.DataFrame(scaled_pred, columns=Y_train.columns)

# Inverse transform the prediction
# First reverse the standard scaling
nn_pred = scaler_targets.inverse_transform(scaled_pred_df)  # Inverse Standard Scaler

# Convert back to DataFrame if needed (if 'inverse_transform' returns an array)
nn_pred_df = pd.DataFrame(nn_pred, columns=Y_train.columns)

# Then reverse the Yeo-Johnson transformation
nn_predictions = scaler_yeo.inverse_transform(nn_pred_df)  # Inverse Yeo-Johnson

# Calculate MSE and R^2 Score
nn_mse = mean_squared_error(Y_test, nn_predictions)
nn_r2 = r2_score(Y_test, nn_predictions)
print(f"Neural Network - MSE: {nn_mse:.4f}, R²: {nn_r2:.4f}")


63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 384us/step
Neural Network - MSE: 434.5164, R²: 0.8964


In [ ]:

x = np.array([3.0, 800.0, 300.0, 0.5, 8.0, 6.0])
#x_log = np.log(x + 1)  # Apply log transformation
x_sc = scaler_features.transform([x]) 
pred = model.predict(x_sc)
nn_hops = scaler_targets.inverse_transform(pred)



1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
[8.5398994e+01 4.5393486e+01 9.4838305e+00 2.2457851e-02]


/opt/anaconda3/envs/tad/lib/python3.9/site-packages/sklearn/utils/validation.py:2739: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names



In [51]:
import plotly.graph_objects as go
import pandas as pd

def plot_predictions(predictions, actuals, model_name):
    fig = go.Figure()

    # Short names for each attribute
    short_names = {
        'out:Leftover inventory[m2]': 'Leftover Inventory',
        'out:Displacement Average[cm]': 'Displacement Avg.',
        'out:Uncovered Wall Area[m2]': 'Uncovered Area',
        'out:Average Mapping Tolerance': 'Mapping Tolerance Avg.'
    }

    # Colors for each attribute
    colors = {
        'out:Leftover inventory[m2]': 'rgba(178, 24, 43, 1)',  # Deep red
        'out:Displacement Average[cm]': 'rgba(214, 96, 77, 1)',  # Soft red
        'out:Uncovered Wall Area[m2]': 'rgba(33, 102, 172, 1)',  # Deep blue
        'out:Average Mapping Tolerance': 'rgba(67, 147, 195, 1)'  # Soft blue
    }

    

    # Create a scatter plot for each attribute
    for col in actuals.columns:
        fig.add_trace(go.Scatter(
            x=actuals[col],
            y=predictions[:, actuals.columns.get_loc(col)],
            mode='markers',
            marker=dict(color=colors[col], size=5, opacity=0.5),
            name=short_names[col]
            #name=f'{col}'
        ))

        # Add line for perfect prediction
        min_val = min(actuals[col].min(), predictions[:, actuals.columns.get_loc(col)].min())
        max_val = max(actuals[col].max(), predictions[:, actuals.columns.get_loc(col)].max())
        fig.add_trace(go.Scatter(
            x=[min_val, max_val],
            y=[min_val, max_val],
            mode='lines',
            line=dict(color='black', dash='dash'),
            showlegend=False
        ))

    # Update the layout for the plot, including customizing the legend
    fig.update_layout(
        #title=f'Actual vs Predictions: {model_name}',
        xaxis_title='Ground Truth',
        yaxis_title='Predictions',
        template='plotly_white',
        height=600,
        width=800,
        legend=dict(
            x=1,
            y=1,
            xanchor='right',
            yanchor='bottom',
            orientation='h',
            # bgcolor='rgba(255, 255, 255, 0.5)'  # Optional: adding a background color for clarity
        ),
        font=dict(color='black', size=18),  # Ensure text is black and adjust size as needed
        # Adding a plot border
        xaxis=dict(showline=True, linewidth=2, linecolor='black'),
        yaxis=dict(showline=True, linewidth=2, linecolor='black')
    )
    
    # Show the figure
    fig.show()

plot_predictions(nn_predictions, Y_test, "Neural Network")

In [49]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Calculate errors for each target
error = nn_predictions - Y_test.values

# Short names for each attribute (for cleaner labels)
short_names = {
    'out:Leftover inventory[m2]': 'Leftover Inventory',
    'out:Displacement Average[cm]': 'Displacement Avg.',
    'out:Uncovered Wall Area[m2]': 'Uncovered Area',
    'out:Average Mapping Tolerance': 'Mapping Tolerance Avg.'
}

# Colors for each attribute
colors = {
    'out:Leftover inventory[m2]': 'rgba(178, 24, 43, 1)',  # Deep red
    'out:Displacement Average[cm]': 'rgba(214, 96, 77, 1)',  # Soft red
    'out:Uncovered Wall Area[m2]': 'rgba(33, 102, 172, 1)',  # Deep blue
    'out:Average Mapping Tolerance': 'rgba(67, 147, 195, 1)'  # Soft blue
}

# Create subplots with 1 row and 4 columns
fig = make_subplots(
    rows=1, cols=4, 
    subplot_titles=[short_names[col] for col in Y_test.columns],
    horizontal_spacing=0.1  # Adjust spacing between subplots
)

# Plot histograms for each target with lines around bars
for idx, col in enumerate(Y_test.columns, 1):
    fig.add_trace(
        go.Histogram(
            x=error[:, idx-1],
            name=short_names[col],
            marker=dict(
                color=colors[col],
                line=dict(
                    color='black',  # Add black border around bars
                    width=1         # Border thickness
                )
            ),
            nbinsx=30,
            opacity=0.7,
            showlegend=False  # Hide legend for individual histograms
        ),
        row=1, col=idx  # Place all in the first row
    )

# Update layout
fig.update_layout(
    height=400,  # Adjust height as needed
    width=1600,  # Adjust width for neatness
    title=dict(
        text='Prediction Error Distribution',
        x=0.5,  # Center align the title
        font=dict(size=20)  # Adjust font size
    ),
    template='plotly_white',
    font=dict(size=12),  # Font size for axes and titles
    showlegend=False,  # Hide legend
    #margin=dict(l=20, r=20, t=50, b=50)  # Adjust margins
)

# Update x and y axis labels and add neat spacing
for i in range(1, 5):
    fig.update_xaxes(
        title_text='Prediction Error',
        row=1, col=i,
        showline=True, linewidth=2, linecolor='black',  # Add axis lines
        ticks="outside", tickwidth=2, tickcolor='black'
    )
    fig.update_yaxes(
        title_text='Count',
        row=1, col=i,
        showline=True, linewidth=2, linecolor='black',
        ticks="outside", tickwidth=2, tickcolor='black'
    )

# Show the plot
fig.show()

In [35]:
from sklearn.base import BaseEstimator, RegressorMixin
import numpy as np

class KerasRegressor(BaseEstimator, RegressorMixin):
    def __init__(self, model, scaler=None):
        self.model = model
        self.scaler = scaler  # Optional scaler for preprocessing

    def fit(self, X, y, epochs=100, batch_size=32, verbose=0):
        # Ensure that X and y are numpy arrays
        X = np.array(X)
        y = np.array(y)

        # Scale the data if a scaler is provided
        if self.scaler is not None:
            X = self.scaler.fit_transform(X)

        # Fit the model
        self.model.fit(X, y, epochs=epochs, batch_size=batch_size, verbose=verbose)
        return self

    def predict(self, X):
        # Ensure that X is a numpy array
        X = np.array(X)

        # Scale the data if a scaler is provided
        if self.scaler is not None:
            X = self.scaler.transform(X)

        return self.model.predict(X)

    def score(self, X, y):
        # Calculate the mean squared error as the score
        from sklearn.metrics import mean_squared_error
        y_pred = self.predict(X)
        return -mean_squared_error(y, y_pred)  # Return negative MSE for maximization

# Example usage:
# Assuming `nn_model` is your Keras model and `scaler` is your preprocessing scaler
keras_model = KerasRegressor(model=model, scaler=scaler)
# Now you can use keras_model with scikit-learn functions

# Wrap your Keras model
keras_model = KerasRegressor(model=model)

from sklearn.inspection import permutation_importance

# Compute permutation importance

perm_importance = permutation_importance(keras_model, X_test, Y_test, n_repeats=10, random_state=42)

importance_scores = perm_importance.importances_mean
# Now you can plot or use the importance scores as needed


63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 411us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 349us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 315us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 340us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 327us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 328us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 365us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 337us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 338us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 334us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 333us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 355us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 353us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 348us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 558us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 364us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 327us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 342us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 355us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 336us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 707us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 367us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 334us/step
63/63 ━━━━━━━━━━━━━━━━━━━━ 0s 335us/step
63/63 ━━━━━━━━━━

In [39]:
import plotly.express as px
import pandas as pd

# Create a DataFrame with the importance scores
importance_df = pd.DataFrame({
    'Feature': feature_names,
    'Importance': perm_importance.importances_mean
})

# Sort by importance
importance_df = importance_df.sort_values('Importance', ascending=True)

# Create the horizontal bar plot with custom color #053061
fig = px.bar(
    importance_df,
    x='Importance',
    y='Feature',
    orientation='h',
    template='plotly_white',
    color_discrete_sequence=['#053061']  # Set the bar color
)

# Update layout
fig.update_layout(
    height=600,
    width=1000,
    title='Feature Importance',
    xaxis_title='Permutation Importance Score',
    yaxis_title='Features',
    font=dict(size=18),
    # Adding a plot border
    xaxis=dict(showline=True, linewidth=2, linecolor='black'),
    yaxis=dict(showline=True, linewidth=2, linecolor='black')
)

# Show the plot
fig.show()